In [1]:
%matplotlib inline

In [2]:
!ls

Dataset Preparation .ipynb		  results.png
depth_1_train_ann.txt			  RGB Small Few Shot Dataset .ipynb
depth-batch.sh				  sample-batch.sh
Depth Dataset Preparation.ipynb		  slurm-3526628.out
Depth Few Shot Dataset Preparation.ipynb  slurm-3526629.out
depth.mp4				  slurm-3526630.out
dist_evaluation.py			  test_dist.sh
evaluation				  Testing Augmentations.ipynb
evaluation.py				  test.sh
Few-Shot Dataset Preparation.ipynb	  train-depth-config-1.py
few-shot-fine-tune-config-frozen.py	  train-depth-config.py
fine-tune-config-frozen.py		  train.sh
fine-tune-config.py			  unfrozen-batch.sh
frozen-batch.sh				  untitled
graph.png				  utils.py
loader.py				  validation
make_graph.sh				  Video-Swin-Training-Pipeline.ipynb
Multi-sized Dataset Preparation.ipynb	  Video-Swin-Train-Pipeline.py
(Old) Visualize Performance.ipynb	  visualization.png
__pycache__				  Visualize Performance-Copy1.ipynb
README.md				  Visualize Performance.ipynb
results.pdf				  work_dirs


In [3]:
import numpy as np
import re
from utils import show_video
from glob import glob

In [4]:
DATASET_PATH = '/vision/group/ntu-rgbd/'

In [5]:
!ls $DATASET_PATH

alan				    flow_s012
cflow_kmeans_s001		    flow_s013
cflow_kmeans_s002		    flow_s014
cflow_kmeans_s003		    flow_s015
cflow_kmeans_s004		    flow_s016
cflow_kmeans_s005		    flow_s017
cflow_kmeans_s006		    mask_s001
cflow_kmeans_s007		    mask_s002
cflow_kmeans_s008		    mask_s003
cflow_kmeans_s009		    mask_s004
cflow_kmeans_s010		    mask_s005
cflow_kmeans_s011		    mask_s006
cflow_kmeans_s012		    mask_s007
cflow_kmeans_s013		    mask_s008
cflow_kmeans_s014		    mask_s009
cflow_kmeans_s015		    mask_s010
cflow_kmeans_s016		    mask_s011
cflow_kmeans_s017		    mask_s012
cflow_uniform_s001		    mask_s013
cflow_uniform_s002		    mask_s014
cflow_uniform_s003		    mask_s015
cflow_uniform_s004		    mask_s016
cflow_uniform_s005		    mask_s017
cflow_uniform_s006		    ntu_rgbd_pths.npy
cflow_uniform_s007		    qflow_s001
cflow_uniform_s008		    qflow_s002
cflow_uniform_s009		    qflow_s003
cflow_uniform_s010		    qflow_s004
cflow_uniform_s011		    qflow_s005
cflow_uniform_s012		    qflow_

## Dataset structure
* `depth_s0\*\*` defines a directory of actions performed by a single person (subject 0\*\*)
    * Within each of these subdirectories, the data is formatted as SxxxCxxxPxxxRxxxAxxx
    * S is the setup number (I believe this is the room/background)
    * C is camera ID
    * P is the performer (subject ID)
    * R is replication number (1 or 2 if done multiple times)
    * A is action class label

In [6]:
!ls {DATASET_PATH + 'depth_s001'}

S001C001P001R001A001  S001C002P001R001A001  S001C003P001R001A001
S001C001P001R001A002  S001C002P001R001A002  S001C003P001R001A002
S001C001P001R001A003  S001C002P001R001A003  S001C003P001R001A003
S001C001P001R001A004  S001C002P001R001A004  S001C003P001R001A004
S001C001P001R001A005  S001C002P001R001A005  S001C003P001R001A005
S001C001P001R001A006  S001C002P001R001A006  S001C003P001R001A006
S001C001P001R001A007  S001C002P001R001A007  S001C003P001R001A007
S001C001P001R001A008  S001C002P001R001A008  S001C003P001R001A008
S001C001P001R001A009  S001C002P001R001A009  S001C003P001R001A009
S001C001P001R001A010  S001C002P001R001A010  S001C003P001R001A010
S001C001P001R001A011  S001C002P001R001A011  S001C003P001R001A011
S001C001P001R001A012  S001C002P001R001A012  S001C003P001R001A012
S001C001P001R001A013  S001C002P001R001A013  S001C003P001R001A013
S001C001P001R001A014  S001C002P001R001A014  S001C003P001R001A014
S001C001P001R001A015  S001C002P001R001A015  S001C003P001R001A015
S001C001P001R001A016  S00

In [7]:
show_video(DATASET_PATH + 'depth_s003/S003C001P001R001A001/')

In [8]:
# Cross-setup evaluation uses even setupIDs for training, odd setupIDs for testing
# Cross-subject evaluation is as follows:
# Person IDs for training:
#1, 2, 4, 5, 8, 9, 13, 14, 15, 16, 17, 18, 19, 25, 27, 28, 31, 34, 35,
#38, 45, 46, 47, 49, 50, 52, 53, 54, 55, 56, 57, 58, 59, 70, 74, 78,
#80, 81, 82, 83, 84, 85, 86, 89, 91, 92, 93, 94, 95, 97, 98, 100, 103.
# Rest are for testing
trainIDs = set([1, 2, 4, 5, 8, 9, 13, 14, 15, 16, 17, 18, 19, 25, 27, 28, 31, 34, 35,
38, 45, 46, 47, 49, 50, 52, 53, 54, 55, 56, 57, 58, 59, 70, 74, 78,
80, 81, 82, 83, 84, 85, 86, 89, 91, 92, 93, 94, 95, 97, 98, 100, 103])

In [22]:
# Gets the person id from a video filename string
def get_person_id(video_file):
    p_idx = video_file.find("P")
    return int(video_file[p_idx+1:p_idx+4])

def is_training_set(video_file):
    return get_person_id(video_file) in trainIDs

def get_label(video_file):
    l_idx = video_file.find("A")
    return int(video_file[l_idx+1:]) - 1 # Action 1 corresponds to label 0

def get_alabel(video_file):
    l_idx = video_file.find("A")
    return int(video_file[l_idx+1:]) # Action 1 corresponds to label 1

def get_num_frames(video_file):
    return len(glob(video_file + '/*'))

In [10]:
get_person_id(DATASET_PATH + 'depth_s003/S003C001P001R001A001/')

1

In [11]:
is_training_set(DATASET_PATH + 'depth_s003/S003C001P002R001A001/')

True

In [12]:
# Get the depth training set paths
# SINCE THIS IS RANDOM, need to ensure consistency with rgb and depth frames,
# so have to use different system and load from rgb frames
file_dirs = glob(DATASET_PATH + "depth_s*/")

In [91]:
rgb_val_pths = np.load(DATASET_PATH + 'few-shot-rgb-val-paths.npy')
rgb_train_pths = np.load(DATASET_PATH + 'few-shot-rgb-train-paths.npy')
rgb_sup_pths = np.load(DATASET_PATH + 'few-shot-rgb-support-paths.npy')
rgb_sup_val_pths = np.load(DATASET_PATH + 'few-shot-rgb-support-val-paths.npy')

In [92]:
print(len(rgb_train_pths))

33526


In [93]:
support_set = set([1, 7, 13, 19, 25, 31, 37, 43, 49, 55, 61, 67, 73, 79, 85, 91, 97, 103, 109, 115])
full_set = set([i for i in range(1, 61)])  #121
train_set = full_set - support_set

In [94]:
max_per_class = 100
lab2paths = {}
for lab in train_set:
    lab2paths[lab] = []

In [95]:
for path in rgb_train_pths:
    alabel = get_alabel(path)
    if len(lab2paths[alabel]) < max_per_class:
        lab2paths[alabel].append(path)

In [97]:
total = 0
for lab in train_set:
    total += len(lab2paths[lab])


In [98]:
rgb_train_pths = []
for lab in train_set:
    rgb_train_pths += lab2paths[lab]

In [99]:
np.save(DATASET_PATH + str(max_per_class) + '-few-shot-rgb-train-paths.npy', rgb_train_pths)

In [ ]:
# Generate training annotation file
num_empty_vids = 0
ann_filename = DATASET_PATH + str(max_per_class) + '_few_shot_rgb_train_ann.txt'
with open(ann_filename, "w") as f:
    for path in rgb_train_pths:
        num_frames = get_num_frames(path)
        label = get_label(path)
        if num_frames > 0:
            f.write(path + ' ' + str(num_frames) + ' ' + str(label) + '\n')
        else:
            num_empty_vids += 1
print("Emtpy vids:", num_empty_vids)

### Create depth as well 

In [22]:
rgb_ann_filename = DATASET_PATH + str(max_per_class) + '-few_shot_rgb_support_test_ann.txt'
depth_ann_filename = DATASET_PATH + str(max_per_class) + '-few_shot_depth_support_test_ann.txt'
with open(rgb_ann_filename, "r") as f:
    with open(depth_ann_filename, "w") as w:
        for line in f.readlines():
            new_line = rgb2depth(line)
            w.write(new_line)